In [60]:
load("skeinslib.sage")

In [18]:
T = matrix(ZZ, 2, [1, 1, 0, 1])

In [19]:
T

[1 1]
[0 1]

In [55]:
compute_reduced_matrix(T, 4, True)

Calculating relations for level 4 (81 lattice points) ...
Found 1060 (non-independent) relations. Reducing ...
Calculating relations for level 3 (49 lattice points) ...
[(sqq^(-3), (3, 0)), (-sqq^2, (2, 0))]
[(1, (0, 0)), (-1/sqq^9, (3, 0))]
Found 486 (non-independent) relations. Reducing ...
Calculating relations for level 2 (25 lattice points) ...
[(sqq^(-2), (2, 0)), (-sqq, (1, 0))]
Found 166 (non-independent) relations. Reducing ...
Calculating relations for level 1 (9 lattice points) ...
[(1/sqq, (1, 0)), (-1, (0, 0))]
Found 28 (non-independent) relations.

Dimension estimate for empty skein part at level 1: 1.

Visualisation:

. | . 
- x - 
. | . 

Dimension estimate for empty skein part at level 2: 1.

Visualisation:

. . | . . 
. . | . . 
- - x - - 
. . | . . 
. . | . . 

Dimension estimate for empty skein part at level 3: 1.

Visualisation:

. . . | . . . 
. . . | . . . 
. . . | . . . 
- - - x - - - 
. . . | . . . 
. . . | . . . 
. . . | . . . 

Dimension estimate for empty sk

(1740 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field,
 1740 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field,
 [1, 1, 1, 1])

In [15]:
v_1 = vector(ZZ, [0, 0], immutable = True)

In [16]:
v_2 = vector(ZZ, [1, 0], immutable = True)

In [21]:
get_relation(T, v_1, v_2)

[(1, (1, 0)), (-1, (1, 0))]

In [22]:
get_relation(T, vector(ZZ, [0, 1], immutable = True), vector(ZZ, [1, -1], immutable = True))

[(1/sqq, (1, 0)), (-1, (0, 0))]

In [23]:
get_relation(T, vector(ZZ, [0, 1], immutable = True), vector(ZZ, [2, -1], immutable = True))

[(sqq^(-2), (2, 0)), (-sqq, (1, 0))]

In [24]:
get_relation(T, vector(ZZ, [0, 1], immutable = True), vector(ZZ, [3, -1], immutable = True))

[(sqq^(-3), (3, 0)), (-sqq^2, (2, 0))]

In [29]:
get_relation(T, vector(ZZ, [0, -3], immutable = True), vector(ZZ, [0, 3], immutable = True))

[(1, (0, 0)), (-1/sqq^9, (3, 0))]

In [47]:
compute_reduced_matrix(T, 4, True)

Calculating relations for level 4 (81 lattice points) ...
Found 1060 (non-independent) relations. Reducing ...
Calculating relations for level 3 (49 lattice points) ...
Found 486 (non-independent) relations. Reducing ...
Calculating relations for level 2 (25 lattice points) ...
Found 166 (non-independent) relations. Reducing ...
Calculating relations for level 1 (9 lattice points) ...
Found 28 (non-independent) relations.

Dimension estimate for empty skein part at level 1: 1.

Visualisation:

. | . 
- x - 
. | . 

Dimension estimate for empty skein part at level 2: 1.

Visualisation:

. . | . . 
. . | . . 
- - x - - 
. . | . . 
. . | . . 

Dimension estimate for empty skein part at level 3: 1.

Visualisation:

. . . | . . . 
. . . | . . . 
. . . | . . . 
- - - x - - - 
. . . | . . . 
. . . | . . . 
. . . | . . . 

Dimension estimate for empty skein part at level 4: 1.

Visualisation:

. . . . | . . . . 
. . . . | . . . . 
. . . . | . . . . 
. . . . | . . . . 
- - - - x - - - - 
. . . 

(1740 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field,
 1740 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field,
 [1, 1, 1, 1])

In [31]:
p_0 = vector(ZZ, [0, 0], immutable=True)

In [35]:
p_1 = vector(ZZ, [1, 0], immutable=True)

In [38]:
p_3 = vector(ZZ, [0, 5], immutable=True)

In [40]:
{p_0} == {v_1, v_2}

False

In [33]:
p_0 in {v_1}

True

In [34]:
type({v_1})

<class 'set'>

In [16]:
def compute_reduced_matrix_alt(gamma, shell_level, interactive_flag, base_level = 1, base_data=None):
    '''
    Computes the reduced matrix of relations at a given shell level, as well as
    its co-rank, which is an estimate of the dimension of the empty part of the
    skein module

    Returns a tuple (A, A_reduced, dim_estimates), where A is the matrix and
    dim_estimates is the list of estimated dimensions for shell levels <= to the
    shell level parameter.

    Works recursively: the relation matrix for level n is built up as

                [[  X  | 0 ]
                 [---------]
                 [relations]]

    where X is the matrix of relations for level n-1, in REF, obtained from a
    recursive call to the function, and the list relations is a list of
    relations at level n that were not already included at level n-1.

    Supports recursion to a specified base_level, with base_data the results of
    a previous call to the function (that is, a tuple of length 3). Usually this
    would be loaded as a sage object saved from a previous session. If the
    recursion base is unspecified then the default is recurse to shell_level 1
    and compute this data from scratch.
    '''
    N = (2*shell_level + 1)**2
    # And the number of points in previous level.
    M = (2*shell_level - 1)**2
    if interactive_flag:
        print("Calculating relations for level %d (%d lattice points) ..." % (shell_level, N))

    # Get the relations new to this shell level.
    relations = get_relations_empty(gamma, shell_level, order_by_shell_level)
    if interactive_flag:
        print("Found %d (non-independent) relations.\n" % len(relations))
    # Form a relation matrix, and reduce it.
    A = matrix(K, relations, sparse=True, immutable=True)
    A_reduced = A.rref()

    # Get the spanning set
    ordering = order_by_shell_level(shell_level)
    spanning_set = get_spanning_set(A_reduced, ordering, shell_level)

    # Base of the recursion: return the reduced matrix and spanning set.
    dim_estimate = len(spanning_set)
    if interactive_flag:
        print("Dimension estimate for empty skein part at level %d: %d.\n\nVisualisation:\n" % (shell_level, dim_estimate))
        print_generators(shell_level, spanning_set, order_by_shell_level)

    return (A, A_reduced, [dim_estimate])


In [4]:
load("skeinslib.sage")

In [ ]:
compute_reduced_matrix_alt(T, 4, True)

Calculating relations for level 4 (81 lattice points) ...
[(1/sqq, (1, 0)), (-1, (0, 0))]
[(sqq^(-2), (2, 0)), (-sqq, (1, 0))]
[(sqq^(-3), (3, 0)), (-sqq^2, (2, 0))]


In [1]:
var('sqq')

sqq

In [2]:
sqq

sqq

In [74]:
v_0 = vector(K, [-1, sqq**(-1), 0, 0], immutable = True)

In [75]:
v_1 = vector(K, [0, -sqq**(1), sqq**(-2), 0], immutable = True)

In [76]:
v_2 = vector(K, [0, 0, -sqq**2, sqq**(-3)], immutable = True)

In [77]:
v_3 = vector(K, [-1, 0, 0, sqq**(-9)], immutable = True)

In [78]:
A = matrix(K, [v_0, v_1, v_2, v_3])

In [79]:
A.rank()

3

In [80]:
v_4 = vector(K, [1, 0, 0, 0], immutable = True)

In [81]:
B = matrix(K, [v_0, v_1, v_2, v_3, v_4])

In [82]:
B.rank()

4

In [84]:
A = compute_reduced_matrix_alt(T, 4, True)

Calculating relations for level 4 (81 lattice points) ...
[(1/sqq, (1, 0)), (-1, (0, 0))]
[(sqq^(-2), (2, 0)), (-sqq, (1, 0))]
[(sqq^(-3), (3, 0)), (-sqq^2, (2, 0))]
[(1, (0, 0)), (-1/sqq^9, (3, 0))]
Found 2878 (non-independent) relations.

Dimension estimate for empty skein part at level 4: 1.

Visualisation:

. . . . | . . . . 
. . . . | . . . . 
. . . . | . . . . 
. . . . | . . . . 
- - - - x - - - - 
. . . . | . . . . 
. . . . | . . . . 
. . . . | . . . . 
. . . . | . . . . 



In [21]:
A

(2878 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field,
 2878 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field,
 [1])

In [22]:
A[0]

2878 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field (use the '.str()' method to see the entries)

In [23]:
A[0].str()

'[                   0                    0                    0                    1                    0                    0                    0                    0                    0                    0                    0                   -1                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0                    0            

In [24]:
A[1].str()

'[        1         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0 -1/sqq^16         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0]\n[        0         1         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0         0      

In [26]:
order = order_by_shell_level(4)

In [27]:
get_spanning_set(A[0], order, 4)

[0]

In [28]:
get_spanning_set(A[1], order, 4)

[0]

In [85]:
B = A[0]

In [30]:
C = A[1]

In [31]:
B.rank()

80

In [38]:
B.ncols()

81

In [34]:
order[vector(ZZ, [0, 0], immutable=True)]

0

In [39]:
basis_elt = vector(K, [1 if i == 0 else 0 for i in range(81)], sparse=True)

In [40]:
B_enlarged = block_matrix([[B], [matrix(basis_elt)]])

In [41]:
B_enlarged.rank()

81

In [42]:
C_enlarged = block_matrix([[C], [matrix(basis_elt)]])

In [43]:
C_enlarged.rank()

81

In [44]:
basis_elt

(1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)

In [45]:
order[vector(ZZ, [1, 0], immutable=True)]

1

In [46]:
order[vector(ZZ, [2, 0], immutable=True)]

9

In [47]:
order[vector(ZZ, [3, 0], immutable=True)]

25

In [56]:
for r in B.rows():
    if r[0] != 0 and r[1] != 0:
        print(r)
        print(B.rows().index(r))
    if r[1] != 0 and r[9] != 0:
        print(r)
        print(B.rows().index(r))
    if r[9] != 0 and r[25] != 0:
        print(r)
        print(B.rows().index(r))
    if r[25] != 0 and r[0] != 0:
        print(r)
        print(B.rows().index(r))

(-1, 1/sqq, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
153
(0, -sqq, 0, 0, 0, 0, 0, 0, 0, 1/sqq^2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
155
(0, 0, 0, 0, 0, 0, 0, 0, 0, -sqq^2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1/sqq^3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
170
(1, -1/sqq, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

(-1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1/sqq^9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
1412
(1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -1/sqq^9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
1442
(1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -1/sqq^9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
1442
(1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -1/sqq^9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [51]:
for r in C.rows():
    if r[0] != 0 and r[1] != 0:
        print(r)
    if r[1] != 0 and r[9] != 0:
        print(r)
    if r[9] != 0 and r[25] != 0:
        print(r)
    if r[25] != 0 and r[0] != 0:
        print(r)

In [70]:
M = matrix(K, [B[153], B[155], B[170], B[1412]])

In [71]:
M.rank()

3

In [72]:
M

4 x 81 sparse matrix over Fraction Field of Sparse Univariate Polynomial Ring in sqq over Rational Field (use the '.str()' method to see the entries)

In [73]:
M.str()

'[     -1   1/sqq       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0]\n[      0    -sqq       0       0       0       0       0       0       0 1/sqq^2       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0    

In [87]:
for r in B.rows():
    if r[1] == sqq^(1) and r[9] == -sqq^(-2):
        print(r)
        print(B.rows().index(r))
    if r[1] == -sqq^(1) and r[9] == sqq^(-2):
        print(r)
        print(B.rows().index(r))

(0, -sqq, 0, 0, 0, 0, 0, 0, 0, 1/sqq^2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
155
(0, sqq, 0, 0, 0, 0, 0, 0, 0, -1/sqq^2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
209
(0, -sqq, 0, 0, 0, 0, 0, 0, 0, 1/sqq^2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
155
(0, sqq, 0, 0, 0, 0, 0, 0, 0, -1/sqq^2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 